## This notebook provides some simple illustrations to the course Many-body physics and quantum computation, delivered by Kareljan Schoutens at the GGI SFT 2022 PhD School, February 2022

### Goal: express CNOT in terms of native gates for Heisenberg XXX interaction


In [1]:
import cirq
import numpy as np

Set up two qubits

In [2]:
qubits = cirq.LineQubit.range(2)

Define the HeisGate on two qubits by ${\rm HEIS}(\alpha) = e^{- i \alpha/4} e^{- i \alpha \bf{S}^{(1)}\cdot\bf{S}^{(2)}}$,

In [3]:
class HeisGate(cirq.Gate):
    def __init__(self, alpha):
        super(HeisGate, self)
        self.alpha = alpha
    
    def _num_qubits_(self):
        return 2

    def _unitary_(self):
        return np.array([
            [np.exp(- 1.0j * self.alpha/2),  0.0, 0.0,  0.0],
            [0.0,  np.cos(self.alpha/2), -1.0j * np.sin(self.alpha/2),  0.0],
            [0.0,  -1.0j * np.sin(self.alpha/2), np.cos(self.alpha/2),  0.0],
            [0.0,  0.0, 0.0, np.exp(- 1.0j * self.alpha/2)]
        ])
    
    def _circuit_diagram_info_(self, args):
        return f"Heis({np.around(self.alpha,4)})", f"Heis({np.around(self.alpha,4)})"

def Heis_layer(angle):
    yield HeisGate(angle).on(cirq.LineQubit(0),cirq.LineQubit(1))


Check unitarity of ${\rm HEIS}(\alpha)$

In [4]:
alpha=np.pi/7

Unit_Heis=np.array([
            [np.exp(- 1.0j * alpha/2),  0.0, 0.0,  0.0],
            [0.0,  np.cos(alpha/2), -1.0j * np.sin(alpha/2),  0.0],
            [0.0,  -1.0j * np.sin(alpha/2), np.cos(alpha/2),  0.0],
            [0.0,  0.0, 0.0, np.exp(- 1.0j * alpha/2)]])

# print(np.around(Unit_Heis,4))
# print("")

Unit_Heis_dag=np.conj(Unit_Heis.T)

# print(np.around(Unit_Heis_dag,4))
# print("")

print("Product Conjugate[HEIS(alpha) times HEIS(alpha)")
print()
print(np.around(np.dot(Unit_Heis,Unit_Heis_dag),2))

Product Conjugate[HEIS(alpha) times HEIS(alpha)

[[1.+0.j 0.+0.j 0.+0.j 0.+0.j]
 [0.+0.j 1.+0.j 0.+0.j 0.+0.j]
 [0.+0.j 0.+0.j 1.+0.j 0.+0.j]
 [0.+0.j 0.+0.j 0.+0.j 1.+0.j]]


Note that ${\rm HEIS}(\pi/2)$ represents the square root of SWAP

In [5]:
alpha=np.pi/2

Unit_Heis=np.array([
            [np.exp(- 1.0j * alpha/2),  0.0, 0.0,  0.0],
            [0.0,  np.cos(alpha/2), -1.0j * np.sin(alpha/2),  0.0],
            [0.0,  -1.0j * np.sin(alpha/2), np.cos(alpha/2),  0.0],
            [0.0,  0.0, 0.0, np.exp(- 1.0j * alpha/2)]])

print("HEIS gate at alpha = pi/2")
print()
print(np.around(Unit_Heis,4))
print()

print("Taking the square")
print()
print(np.around(np.dot(Unit_Heis,Unit_Heis),2))

HEIS gate at alpha = pi/2

[[0.7071-0.7071j 0.    +0.j     0.    +0.j     0.    +0.j    ]
 [0.    +0.j     0.7071+0.j     0.    -0.7071j 0.    +0.j    ]
 [0.    +0.j     0.    -0.7071j 0.7071+0.j     0.    +0.j    ]
 [0.    +0.j     0.    +0.j     0.    +0.j     0.7071-0.7071j]]

Taking the square

[[0.-1.j 0.+0.j 0.+0.j 0.+0.j]
 [0.+0.j 0.+0.j 0.-1.j 0.+0.j]
 [0.+0.j 0.-1.j 0.+0.j 0.+0.j]
 [0.+0.j 0.+0.j 0.+0.j 0.-1.j]]


Now build a circuit that compiles CNOT into native gates for Heisenberg spin qubits

In [6]:
a, b=qubits

circuit = cirq.Circuit(
    cirq.H(b),
    Heis_layer(np.pi/2),
    cirq.Z(a),
    Heis_layer(np.pi/2),
    cirq.S(a),
    cirq.S(b),
    cirq.Z(b),
    cirq.H(b))
    
print(circuit)

0: ───────Heis(1.5708)───Z───Heis(1.5708)───S───────────
          │                  │
1: ───H───Heis(1.5708)───────Heis(1.5708)───S───Z───H───


Extract representation as unitary matrix to check that this acts as CNOT

In [7]:
np.around(cirq.unitary(circuit),4)

array([[ 0.-1.j,  0.+0.j,  0.+0.j,  0.+0.j],
       [ 0.+0.j,  0.-1.j,  0.+0.j,  0.+0.j],
       [ 0.+0.j,  0.+0.j, -0.+0.j,  0.-1.j],
       [ 0.+0.j,  0.+0.j,  0.-1.j, -0.+0.j]])

With CNOT added the circuit acts as the identity

In [8]:
circuit.append(cirq.CNOT(a,b))
print(circuit)

0: ───────Heis(1.5708)───Z───Heis(1.5708)───S───────────@───
          │                  │                          │
1: ───H───Heis(1.5708)───────Heis(1.5708)───S───Z───H───X───


In [9]:
np.around(cirq.unitary(circuit),4)

array([[ 0.-1.j,  0.+0.j,  0.+0.j,  0.+0.j],
       [ 0.+0.j,  0.-1.j,  0.+0.j,  0.+0.j],
       [ 0.+0.j,  0.+0.j,  0.-1.j, -0.+0.j],
       [ 0.+0.j,  0.+0.j, -0.+0.j,  0.-1.j]])